In [1]:
import numpy as np
import pandas as pd
from pathlib import Path
import re
import golf_stats_lib as gs

In [2]:
gs?

Type:        module
String form: <module 'golf_stats_lib' from 'r:\\learn\\ds_intro\\golf_stats_lib.py'>
File:        r:\learn\ds_intro\golf_stats_lib.py
Docstring:  
Module to provide functions related to obtaining statistics from PGA web site and saving to local CSV files.
   As well as functions to retrieve the data in the CSVs and build DataFrames to hold a specified dataset.

File: ./ds_intro/golf_stats_lib.py

  - tied to various Too Old To Code blog posts
  - function(s) to obtain data from PGA web site and save to local CSV files
  - functions(s) to process the CSV files into DataFrames in various ways
  - built on Jypyter notebook pandas_play_8.ipynb
  
Module level and/or global variables:
----

These may require updating if you add events or stat types.

events - dictionary of currently available events providing PGA Tour ids
stats - dictionary of currently available stat types providing PGA Tour ids
st_cols - for each stat type, a list of table columns to save to csv
d_dir 

In [3]:
gs.tourney_2_df?

Signature: gs.tourney_2_df(t_yr, t_id, psts)
Docstring:
Combine all requested stats for a given tournament and year into a single DataFrame. 
Return DataFrame.
Useage: tourney_2_df(t_yr, t_id, p_sts)
  where t_yr = tournament year
        t_id = tournament id (e.g. 'pga')
        psts = list of player stats (e.g. ['drv', 'gir'])
File:      r:\learn\ds_intro\golf_stats_lib.py
Type:      function


In [4]:
df1 = gs.csv_2_df_base('2019', 'pga', 'drv')
display(df1)

drv
PLAYER NAME             
Dustin Johnson     335.6
Luke List          319.0
Phil Mickelson     318.6
Rory McIlroy       317.4
Lucas Bjerregaard  316.6
...                  ...
Marty Jertson      281.9
Rich Beem          281.9
Henrik Stenson     281.0
Brandt Snedeker    279.8
Andrew Putnam      274.1

[82 rows x 1 columns]

In [5]:
df2 = gs.csv_2_df_base('2019', 'pga', 'gir')
df3 = pd.concat([df1, df2])
display(df3)

drv    gir
PLAYER NAME                     
Dustin Johnson      335.6    NaN
Luke List           319.0    NaN
Phil Mickelson      318.6    NaN
Rory McIlroy        317.4    NaN
Lucas Bjerregaard   316.6    NaN
...                   ...    ...
Rafa Cabrera Bello    NaN  47.22
Ryan Vermeer          NaN  47.22
Pat Perez             NaN  47.22
Rich Beem             NaN  47.22
Marty Jertson         NaN  41.67

[164 rows x 2 columns]

In [6]:
# not what I would expect
# let's sort the dataframe on the player index
#print(type(df3.index[0]))
#print(df3.index)
df_sort = gs.sort_player_name(df3)
display(df_sort)
# OOPS! don't currently have a fix

ValueError: cannot reindex from a duplicate axis

In [7]:
df3 = pd.concat([df1, df2], axis=1)
df_sort = gs.sort_player_name(df3)
display(df_sort)

drv    gir
PLAYER NAME                       
Abraham Ancer         285.6  56.94
Kiradech Aphibarnrat  284.0  54.17
Rich Beem             281.9  47.22
Rafa Cabrera Bello    292.3  47.22
Daniel Berger         301.5  55.56
...                     ...    ...
Jimmy Walker          304.6  69.44
Matt Wallace          300.3  56.94
Danny Willett         307.0  69.44
Aaron Wise            301.0  59.72
Gary Woodland         311.4  70.83

[82 rows x 2 columns]

In [8]:
df4 = gs.csv_2_df_base('2019','rbch','gir')
#display(df4)
df5 = pd.concat([df3, df4], axis=1)
#display(df5)
df_sort = gs.sort_player_name(df5)
display(df_sort)

drv    gir    gir
PLAYER NAME                              
Abraham Ancer         285.6  56.94    NaN
Kiradech Aphibarnrat  284.0  54.17    NaN
Ryan Armour             NaN    NaN  55.56
Rich Beem             281.9  47.22    NaN
Rafa Cabrera Bello    292.3  47.22  58.33
...                     ...    ...    ...
Boo Weekley             NaN    NaN  59.72
Richy Werenski          NaN    NaN  47.22
Danny Willett         307.0  69.44    NaN
Aaron Wise            301.0  59.72    NaN
Gary Woodland         311.4  70.83    NaN

[124 rows x 3 columns]

In [9]:
# unfortunately the above does not tell us to which tournament and year the stat belongs
# and likely not something we want to keep track of separately
# So let's try adding that info to each csv dataframe
df6 = gs.csv_2_df_base('2019', 'pga', 'drv')
cols = pd.MultiIndex.from_tuples([('2019', 'pga', 'drv')])
#midx = pd.MultiIndex(levels=[['zero', 'one'], ['x','y']], labels=[[1,1,0,],[1,0,1,]])
df6.columns = cols
df6 = gs.sort_player_name(df6)
display(df6)

2019
                        pga
                        drv
PLAYER NAME                
Abraham Ancer         285.6
Kiradech Aphibarnrat  284.0
Rich Beem             281.9
Rafa Cabrera Bello    292.3
Daniel Berger         301.5
...                     ...
Jimmy Walker          304.6
Matt Wallace          300.3
Danny Willett         307.0
Aaron Wise            301.0
Gary Woodland         311.4

[82 rows x 1 columns]

In [10]:

# now another stat same year and tourney
df7 = gs.csv_2_df_base('2019', 'pga', 'gir')
cols = pd.MultiIndex.from_tuples([('2019', 'pga', 'gir')])
df7.columns = cols
df7 = gs.sort_player_name(df7)
df_comb1 = pd.concat([df6, df7], axis=1)
display(df_comb1.head())
display(df_comb1.loc['Rory McIlroy'])

2019       
                        pga       
                        drv    gir
PLAYER NAME                       
Abraham Ancer         285.6  56.94
Kiradech Aphibarnrat  284.0  54.17
Rich Beem             281.9  47.22
Rafa Cabrera Bello    292.3  47.22
Daniel Berger         301.5  55.56

2019  pga  drv    317.40
           gir     65.28
Name: Rory McIlroy, dtype: float64

In [11]:
# and a different tournament
df8 = gs.csv_2_df_base('2019', 'rbch', 'gir')
cols = pd.MultiIndex.from_tuples([('2019', 'rbch', 'gir')])
df8.columns = cols
df8 = gs.sort_player_name(df8)
df_comb2 = pd.concat([df6, df7, df8], axis=1)
df_comb2 = gs.sort_player_name(df_comb2)
display(df_comb2)

2019              
                        pga          rbch
                        drv    gir    gir
PLAYER NAME                              
Abraham Ancer         285.6  56.94    NaN
Kiradech Aphibarnrat  284.0  54.17    NaN
Ryan Armour             NaN    NaN  55.56
Rich Beem             281.9  47.22    NaN
Rafa Cabrera Bello    292.3  47.22  58.33
...                     ...    ...    ...
Boo Weekley             NaN    NaN  59.72
Richy Werenski          NaN    NaN  47.22
Danny Willett         307.0  69.44    NaN
Aaron Wise            301.0  59.72    NaN
Gary Woodland         311.4  70.83    NaN

[124 rows x 3 columns]

In [12]:
#df_comb2.columns
df_comb2.columns.names = ['year', 'event', 'stat']
filter = df_comb2.columns.get_level_values('stat') == 'gir'
df_comb2.iloc[:, filter].dropna(how='all')

year                   2019       
event                   pga   rbch
stat                    gir    gir
PLAYER NAME                       
Abraham Ancer         56.94    NaN
Kiradech Aphibarnrat  54.17    NaN
Ryan Armour             NaN  55.56
Rich Beem             47.22    NaN
Rafa Cabrera Bello    47.22  58.33
...                     ...    ...
Boo Weekley             NaN  59.72
Richy Werenski          NaN  47.22
Danny Willett         69.44    NaN
Aaron Wise            59.72    NaN
Gary Woodland         70.83    NaN

[124 rows x 2 columns]

In [13]:
# add another year
# was going to try the append() method, but...
df9 = gs.csv_2_df_base('2020', 'pga', 'drv')
cols = pd.MultiIndex.from_tuples([('2020', 'pga', 'drv')])
#midx = pd.MultiIndex(levels=[['zero', 'one'], ['x','y']], labels=[[1,1,0,],[1,0,1,]])
df9.columns = cols
df_comb2 = pd.concat([df6, df7, df8, df9], axis=1)
df_comb2.columns.names = ['year', 'event', 'stat']
df_comb2 = gs.sort_player_name(df_comb2)
display(df_comb2)

year                   2019                 2020
event                   pga          rbch    pga
stat                    drv    gir    gir    drv
PLAYER NAME                                     
Byeong Hun An           NaN    NaN    NaN  286.6
Abraham Ancer         285.6  56.94    NaN  295.6
Kiradech Aphibarnrat  284.0  54.17    NaN    NaN
Ryan Armour             NaN    NaN  55.56    NaN
Rich Beem             281.9  47.22    NaN    NaN
...                     ...    ...    ...    ...
Danny Willett         307.0  69.44    NaN    NaN
Aaron Wise            301.0  59.72    NaN    NaN
Matthew Wolff           NaN    NaN    NaN  303.8
Gary Woodland         311.4  70.83    NaN  293.0
Tiger Woods             NaN    NaN    NaN  304.0

[153 rows x 4 columns]

In [14]:
filter = df_comb2.columns.get_level_values('stat') == 'drv'
df_comb2.iloc[:, filter].dropna(how='any')

year                   2019   2020
event                   pga    pga
stat                    drv    drv
PLAYER NAME                       
Abraham Ancer         285.6  295.6
Daniel Berger         301.5  291.9
Patrick Cantlay       314.6  295.3
Paul Casey            305.6  295.8
Cameron Champ         313.8  321.1
Joel Dahmen           295.8  289.5
Jason Day             310.0  295.0
Tony Finau            314.3  305.3
Tommy Fleetwood       301.3  305.5
Emiliano Grillo       302.9  287.4
Adam Hadwin           285.8  282.9
Billy Horschel        296.1  284.4
Harold Varner III     308.3  286.8
Dustin Johnson        335.6  305.0
Sung Kang             308.1  292.9
Kurt Kitayama         315.3  302.9
Brooks Koepka         313.0  295.8
Danny Lee             306.5  291.0
Haotong Li            293.9  304.1
Luke List             319.0  299.6
Adam Long             291.5  285.4
Shane Lowry           300.0  287.6
Joost Luiten          284.9  286.0
Hideki Matsuyama      303.5  285.3
Rory McIlroy          317.4  312.5
Phil Mickelson        318.6  293.1
Alex Noren            298.0  289.0
Louis Oosthuizen      306.0  284.6
J.T. Poston           291.5  291.6
Chez Reavie           289.1  274.5
Erik van Rooyen       305.3  295.3
Justin Rose           309.6  294.4
Xander Schauffele     307.0  302.3
Adam Scott            301.5  299.1
Webb Simpson          295.3  281.1
Cameron Smith         302.5  286.3
Brandt Snedeker       279.8  280.9
Jordan Spieth         303.3  295.9
Michael Lorenzo-Vera  302.0  287.6
Matt Wallace          300.3  286.6
Gary Woodland         311.4  293.0

Let's have a look at pd.merge() and joins.

In [15]:
from IPython.display import display_html
def display_side_by_side(*args):
    html_str=''
    for df in args:
        html_str += df.to_html()
    display_html(html_str.replace('table','table style="display:inline; margin:4px; border:none"'),raw=True)
    
    #https://stackoverflow.com/questions/38783027/jupyter-notebook-display-two-pandas-tables-side-by-side

In [16]:
def get_small_df(t_yr, t_id, p_st):
    col_nms = {'drv': {'AVG.': 'drv'},
              'gir': {'%': 'gir'},
              'scramble': {'%': 'scramble'}
    }
    csv_fl = gs.get_csv_nm(t_yr, t_id, p_st)
    get_col = list(col_nms[p_st].keys())[0]
    df_t = pd.read_csv(csv_fl, usecols=[get_col, 'PLAYER NAME'])
    df_t.rename(columns=col_nms[p_st], inplace=True)
    #df1 = gs.sort_player_name(df1)
    #df1.index = sorted(df1['PLAYER NAME'],key=lambda x: re.split(r'\W+', x)[-1])
    #print(df1['PLAYER NAME'].str.extractall(r'(\W+)$'))
    df_t['surnm'] = df_t['PLAYER NAME'].apply(lambda x: re.split(r'\W+', x)[-1])
    df_t = df_t.sort_values(by='surnm').drop(['surnm'], axis=1)
    df_t = df_t.iloc[8:13, :]
    return df_t


In [17]:
df1 = get_small_df('2020', 'pga', 'drv')
df2 = get_small_df('2020', 'pga', 'gir')
df3 = pd.merge(df1, df2)
display_side_by_side(df1, df2, df3)

PLAYER NAME 
 drv 
 
 
 
 
 28 
 Jason Day 
 295.0 
 
 
 1 
 Bryson DeChambeau 
 318.1 
 
 
 19 
 Harris English 
 297.1 
 
 
 5 
 Tony Finau 
 305.3 
 
 
 4 
 Tommy Fleetwood 
 305.5 
 
 
 
 
 
 
 PLAYER NAME 
 gir 
 
 
 
 
 2 
 Jason Day 
 76.39 
 
 
 23 
 Bryson DeChambeau 
 66.67 
 
 
 75 
 Harris English 
 52.78 
 
 
 5 
 Tony Finau 
 72.22 
 
 
 40 
 Tommy Fleetwood 
 63.89 
 
 
 
 
 
 
 PLAYER NAME 
 drv 
 gir 
 
 
 
 
 0 
 Jason Day 
 295.0 
 76.39 
 
 
 1 
 Bryson DeChambeau 
 318.1 
 66.67 
 
 
 2 
 Harris English 
 297.1 
 52.78 
 
 
 3 
 Tony Finau 
 305.3 
 72.22 
 
 
 4 
 Tommy Fleetwood 
 305.5 
 63.89

In [18]:
# couldn't get this to work
def disp_sd_by_sd(*dfs, caps=None):
    stylers = []
    space = "\xa0" * 10
    space = ""
    cnt = 0
    for df in dfs:
        if caps:
            stylers.append(df.style.set_table_attributes("style='display:inline'").set_caption(caps[cnt]))
        else:
            stylers.append(df.style.set_table_attributes("style='display:inline'"))
        cnt += 1
    str_html = ""
    for sts in stylers:
        if str_html:
            str_html += space
        str_html += sts._repr_html_()
    display(str_html)
    

In [19]:
# can specify column(s) to use if desired
df4 = pd.merge(df1, df2, on=['PLAYER NAME'], sort=False)
display_side_by_side(df3, df4)

PLAYER NAME 
 drv 
 gir 
 
 
 
 
 0 
 Jason Day 
 295.0 
 76.39 
 
 
 1 
 Bryson DeChambeau 
 318.1 
 66.67 
 
 
 2 
 Harris English 
 297.1 
 52.78 
 
 
 3 
 Tony Finau 
 305.3 
 72.22 
 
 
 4 
 Tommy Fleetwood 
 305.5 
 63.89 
 
 
 
 
 
 
 PLAYER NAME 
 drv 
 gir 
 
 
 
 
 0 
 Jason Day 
 295.0 
 76.39 
 
 
 1 
 Bryson DeChambeau 
 318.1 
 66.67 
 
 
 2 
 Harris English 
 297.1 
 52.78 
 
 
 3 
 Tony Finau 
 305.3 
 72.22 
 
 
 4 
 Tommy Fleetwood 
 305.5 
 63.89

In [20]:
# let's try using multiple columns
left = pd.DataFrame(
    {
        'firstname': ['John', 'Frank', 'Harry', 'Morris', 'Joseph'],
        'surname': ['Smith', 'Smith', 'Brown', 'White', 'Black'],
        'drv1': df1.drv.to_list(),
        'gir1': df2.gir.to_list()
    }
)
right = pd.DataFrame(
    {
        'firstname': ['John', 'Harry', 'Joseph', 'Morris', 'Arthur'],
        'surname': ['Smith', 'Brown', 'Black', 'Brown', 'White'],
        'drv2': df1.drv.to_list(),
        'gir2': df2.gir.to_list()
    }
)
df_comb = pd.merge(left, right, on=['firstname', 'surname'])
# default join is "inner", i.e. intersection
display_side_by_side(left, right)
display(df_comb)

firstname 
 surname 
 drv1 
 gir1 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Frank 
 Smith 
 318.1 
 66.67 
 
 
 2 
 Harry 
 Brown 
 297.1 
 52.78 
 
 
 3 
 Morris 
 White 
 305.3 
 72.22 
 
 
 4 
 Joseph 
 Black 
 305.5 
 63.89 
 
 
 
 
 
 
 firstname 
 surname 
 drv2 
 gir2 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Harry 
 Brown 
 318.1 
 66.67 
 
 
 2 
 Joseph 
 Black 
 297.1 
 52.78 
 
 
 3 
 Morris 
 Brown 
 305.3 
 72.22 
 
 
 4 
 Arthur 
 White 
 305.5 
 63.89

firstname surname   drv1   gir1   drv2   gir2
0      John   Smith  295.0  76.39  295.0  76.39
1     Harry   Brown  297.1  52.78  318.1  66.67
2    Joseph   Black  305.5  63.89  297.1  52.78

In [21]:
# specify 'outer' to get a union
df_union = df_comb = pd.merge(left, right, on=['firstname', 'surname'], sort=False, how='outer')
display_side_by_side(left, right)
display(df_union)

firstname 
 surname 
 drv1 
 gir1 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Frank 
 Smith 
 318.1 
 66.67 
 
 
 2 
 Harry 
 Brown 
 297.1 
 52.78 
 
 
 3 
 Morris 
 White 
 305.3 
 72.22 
 
 
 4 
 Joseph 
 Black 
 305.5 
 63.89 
 
 
 
 
 
 
 firstname 
 surname 
 drv2 
 gir2 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Harry 
 Brown 
 318.1 
 66.67 
 
 
 2 
 Joseph 
 Black 
 297.1 
 52.78 
 
 
 3 
 Morris 
 Brown 
 305.3 
 72.22 
 
 
 4 
 Arthur 
 White 
 305.5 
 63.89

firstname surname   drv1   gir1   drv2   gir2
0      John   Smith  295.0  76.39  295.0  76.39
1     Frank   Smith  318.1  66.67    NaN    NaN
2     Harry   Brown  297.1  52.78  318.1  66.67
3    Morris   White  305.3  72.22    NaN    NaN
4    Joseph   Black  305.5  63.89  297.1  52.78
5    Morris   Brown    NaN    NaN  305.3  72.22
6    Arthur   White    NaN    NaN  305.5  63.89

In [22]:
# or we can use the keys from on frame or the other
# let's try the left
df_left_join = df_comb = pd.merge(left, right, on=['firstname', 'surname'], sort=False, how='left')
display_side_by_side(left, right)
display(df_left_join)

firstname 
 surname 
 drv1 
 gir1 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Frank 
 Smith 
 318.1 
 66.67 
 
 
 2 
 Harry 
 Brown 
 297.1 
 52.78 
 
 
 3 
 Morris 
 White 
 305.3 
 72.22 
 
 
 4 
 Joseph 
 Black 
 305.5 
 63.89 
 
 
 
 
 
 
 firstname 
 surname 
 drv2 
 gir2 
 
 
 
 
 0 
 John 
 Smith 
 295.0 
 76.39 
 
 
 1 
 Harry 
 Brown 
 318.1 
 66.67 
 
 
 2 
 Joseph 
 Black 
 297.1 
 52.78 
 
 
 3 
 Morris 
 Brown 
 305.3 
 72.22 
 
 
 4 
 Arthur 
 White 
 305.5 
 63.89

firstname surname   drv1   gir1   drv2   gir2
0      John   Smith  295.0  76.39  295.0  76.39
1     Frank   Smith  318.1  66.67    NaN    NaN
2     Harry   Brown  297.1  52.78  318.1  66.67
3    Morris   White  305.3  72.22    NaN    NaN
4    Joseph   Black  305.5  63.89  297.1  52.78

In [24]:
left = pd.DataFrame(
    {
        
        'name': ['John', 'Frank', 'Harry', 'Morris', 'Joseph'],
        'department': ['finance', 'sales', 'engineering', 'sales', 'engineering'],
        'location': ['Vancouver', 'Vancouver', 'Vancouver', 'Calgary', 'Calgary'],
    }
)
right = pd.DataFrame(
    {
        'dept': ['engineering', 'finance', 'sales'],
        'supervisor': ['George', 'Helen', 'Barbara']
    }
)
display_side_by_side(left, right)
display(pd.merge(left, right, left_on='department', right_on='dept'))

name 
 department 
 location 
 
 
 
 
 0 
 John 
 finance 
 Vancouver 
 
 
 1 
 Frank 
 sales 
 Vancouver 
 
 
 2 
 Harry 
 engineering 
 Vancouver 
 
 
 3 
 Morris 
 sales 
 Calgary 
 
 
 4 
 Joseph 
 engineering 
 Calgary 
 
 
 
 
 
 
 dept 
 supervisor 
 
 
 
 
 0 
 engineering 
 George 
 
 
 1 
 finance 
 Helen 
 
 
 2 
 sales 
 Barbara

name   department   location         dept supervisor
0    John      finance  Vancouver      finance      Helen
1   Frank        sales  Vancouver        sales    Barbara
2  Morris        sales    Calgary        sales    Barbara
3   Harry  engineering  Vancouver  engineering     George
4  Joseph  engineering    Calgary  engineering     George